# PLC2024 Lecture 10, 13 Feb 2024

### Strings
- Stored on the heap

In [2]:
let mut s = String::from("hello"); // allocates heap space for new String and initializes
s.push_str(", world!"); // push_str() appends a literal to a String
println!("{}", s); // This will print `hello, world!`
println!("Again {}",s);

hello, world!
Again hello, world!


### Copying values, stack
- Value is copied

In [3]:
let mut x = 7;
let mut y = x;
y = 77;
println!("x = {}, y = {}",x,y);

x = 7, y = 77


### Copying values, heap
- Every value on the heap has a unique owner
- Assignment *moves* ownership
- Memory is freed as soon as scope of owner ends

In [4]:
let mut s1 = String::from("hello");
let mut s2 = s1;
s2.push_str(", world");
println!("s1 = {}, s2 = {}", s1, s2); 

Error: borrow of moved value: `s1`

### The `Copy` trait
- Traits are Rust's equivalent of Java interfaces and Python type classes
- For type that have `Copy` trait, values are copied without moving ownership
- All scalar types have this trait: `u16`, `i32`, `f64`, `bool`, `char` etc

### Mutable parameters
- Need to declare `mut` to update in function

In [5]:
fn main(){
    let mut y = 77;
    update(y);
    println!("y is {}",y);
}

fn update(x:i32){
    x = x+5;
    println!("x is {}",x);
}

Error: cannot assign to immutable argument `x`

In [6]:
fn main(){
    let mut y = 77;
    update(y);
    println!("y is {}",y);
}

fn update(mut x:i32){
    x = x+5;
    println!("x is {}",x);
}

In [7]:
main()

x is 82
y is 77


()

### Cloning
- Makes a copy of a heap value

In [8]:
let s1 = String::from("hello");
let s2 = s1.clone();

println!("s1 = {}, s2 = {}", s1, s2);


s1 = hello, s2 = hello


### Transferring ownership via function calls
- Move heap values back and forth

- Here, ownership of `s` moves to function `takes_ownership`

In [9]:
fn main() {
    let s = String::from("hello");  // s comes into scope

    takes_ownership(s);             // s's value moves into function...
                                    // ... no longer valid here
} // s goes out of scope. Since s's value was moved, nothing special happens.

fn takes_ownership(some_string: String) { // some_string comes into scope
    println!("{}", some_string);
} // some_string goes out of scope, `drop` is called, memory is freed



In [10]:
main()

hello


()

- For types with `Copy` trait, the value is copied to the function without moving ownership

In [11]:
fn main() {
    let s = String::from("hello");  // s comes into scope

    takes_ownership(s);             // s's value moves into function...
                                    // ... no longer valid here

    let x = 5;                      // x comes into scope

    makes_copy(x);                  // x would move into the function, but
    println!("x is {}",x);          // i32 is Copy, so okay to still use x
} // x goes out scope, then s.
  // Since s's value was moved, nothing special happens.

fn takes_ownership(some_string: String) { // some_string comes into scope
    println!("{}", some_string);
} // some_string goes out of scope, `drop` is called, memory is freed

fn makes_copy(some_integer: i32) { // some_integer comes into scope
    println!("{}", some_integer);
} // some_integer goes out of scope, nothing special happens.


In [12]:
main()

hello
5
x is 5


()

- Examples of moving heap values in and out of functions
- In `gives_ownership`, the scope of `some_string` ends but the value created is moved to the calling scope by the return and hence persists after the function exits

In [13]:
fn main() {
    let s1 = gives_ownership();         // gives_ownership moves its return
                                        // value into s1

    let s2 = String::from("hello");     // s2 comes into scope

    let s3 = takes_and_gives_back(s2);  // s2 is moved into
                                        // takes_and_gives_back, which also
                                        // moves its return value into s3
} // Here, s3 goes out of scope and is dropped. s2 was moved, so nothing
  // happens. s1 goes out of scope and is dropped.

fn gives_ownership() -> String {             // gives_ownership will move its
                                             // return value into the function
                                             // that calls it

    let some_string = String::from("yours"); // some_string comes into scope

    some_string                              // some_string is returned and
                                             // moves out to the calling
                                             // function
}

// This function takes a String and returns one
fn takes_and_gives_back(a_string: String) -> String { // a_string comes into
                                                      // scope

    a_string  // a_string is returned and moves out to the calling function
}



- Transferring ownership requires clumsy mechanisms to "get back" parameters passed to functions

In [14]:
fn main() {
    let s1 = String::from("hello");
    let (s2, len) = calculate_length(s1);
    println!("The length of '{}' is {}.", s2, len);
}

fn calculate_length(s: String) -> (String, usize) {
    let length = s.len(); // len() returns the length of a String
    (s, length)
}


In [15]:
main()

The length of 'hello' is 5.


()

### References
- Point to a variable that contains a value on the heap
- Avoids moving ownership
- Creating a reference results in *borrowing* the value

In [16]:
fn main() {
    let s1 = String::from("hello");
    let len = calculate_length(&s1);
    println!("The length of '{}' is {}.", s1, len);
}

fn calculate_length(s: &String) -> usize {
    s.len()
}


In [17]:
main()

The length of 'hello' is 5.


()

- Arguments passed as references are not automatically mutable
- Use `&mut` to denote a mutable reference

In [18]:
fn main() {
    let s = String::from("hello");
    change(&s);
}

fn change(some_string: &String) {
    some_string.push_str(", world");
}


Error: cannot borrow `*some_string` as mutable, as it is behind a `&` reference

In [19]:
fn main() {
    let mut s = String::from("hello");
    change(&mut s);
    println!("s is {}",s);
}

fn change(some_string: &mut String) {
    some_string.push_str(", world");
}


In [20]:
main()

s is hello, world


()

### Constraints on mutable references
- One mutable reference is permitted

In [21]:
{
    let mut s = String::from("hello");
    let r1 = &mut s;
    println!("{}", r1);
}

hello


()

- Cannot have two or more mutable references
- Avoids *race conditions* in concurrent programs

In [22]:
{
    let mut s = String::from("hello");

    let r1 = &mut s;
    let r2 = &mut s;

    println!("{}, {}", r1, r2);
}

Error: cannot borrow `s` as mutable more than once at a time

- Here the second mutable reference is created after the first one goes out of scope, so this is fine

In [23]:
{
    let mut s = String::from("hello");

    {
        let r1 = &mut s;
    } // r1 goes out of scope here, so we can make a new reference with no problems.

    let r2 = &mut s;
}


()

- Cannot mix immutable and mutable references
- Again to avoid race conditions

In [24]:
{
    let mut s = String::from("hello");

    let r1 = &s; // no problem
    let r2 = &s; // no problem
    let r3 = &mut s; // BIG PROBLEM

    println!("{}, {}, and {}", r1, r2, r3);
}

Error: cannot borrow `s` as mutable because it is also borrowed as immutable

- Here the last use of `r1` and `r2` occurs before `r3` is declared
- Rust does sophisticated static analysis to determine this at compile time

In [25]:
{
    let mut s = String::from("hello");

    let r1 = &s; // no problem
    let r2 = &s; // no problem
    println!("{} and {}", r1, r2);
    // variables r1 and r2 will not be used after this point

    let r3 = &mut s; // no problem
    println!("{}", r3);

}

hello and hello
hello


()

- Unlike `gives_ownership` earlier, here `dangle` returns a reference
- Potential problem --- when `dangle` exits, `s` goes out of scope and `reference_to_nothing` becomes a *dangling pointer*, pointing to nothing
- Rust catches this as a compile-time error

In [26]:
fn main() {
    let reference_to_nothing = dangle();
}

fn dangle() -> &String {
    let s = String::from("hello");
    &s
}


Error: missing lifetime specifier

### Slices

- A function to compute the length of the first word in a string
- `bytes.iter()` iterates through `bytes`, `enumerate()` returns a pair (index,reference to value), which is deomposed through pattern matching into `(i, &item)`
- `b' '` specifies a byte constant for the space character

In [27]:
fn first_word(s: &String) -> usize {
    let bytes = s.as_bytes();

    for (i, &item) in bytes.iter().enumerate() {
        if item == b' ' {
            return i;
        }
    }

    s.len()
}


- In this function, Rust cannot recognize that the return value is an index into the string
- If we clear the string, the index is no longer valid, but cannot be flagged by compiler

In [28]:
fn main() {
    let mut s = String::from("hello world");

    let word = first_word(&s); // word will get the value 5

    s.clear(); // this empties the String, making it equal to ""

    // word still has the value 5 here, but there's no more string that
    // we could meaningfully use the value 5 with. word is now totally invalid!
}

- Digression on references and scalar variables, to be resolved later

In [29]:
{
    let mut x = 5;
    let y = &mut x;
    *y = 7;
    println!("x is {}, y is {}",x,*y);
}

Error: unused variable: `word`

Error: cannot borrow `x` as immutable because it is also borrowed as mutable

- A string slice is written similar to a slice in Python
- Gives a reference to a substring

In [30]:
{ 
    let s = String::from("hello world");

    let hello = &s[0..5];
    let world = &s[6..11];
}


()

- Rewrite `first_word` to return slice corresponding to first word
- Will examine distinction between `&String` and `&str` later

In [31]:
fn first_word(s: &String) -> &str {
    let bytes = s.as_bytes();

    for (i, &item) in bytes.iter().enumerate() {
        if item == b' ' {
            return &s[0..i];
        }
    }

    &s[..]
}


- Now, if we try to clear the "parent" string while holding a reference to a substring, it is a compile error
- Another example of combining immutable and mutable references --- the call `s.clear()` implicitly passes a mutable reference to `s` to `clear()`, while `word` currently holds an immutable reference

In [32]:
fn main() {
    let mut s = String::from("hello world");

    let word = first_word(&s);

    s.clear(); // error!

    println!("the first word is: {}", word);
}


Error: cannot borrow `s` as mutable because it is also borrowed as immutable